In [1]:
import itertools
import multiprocessing
import pandas as pd
import os
import random
import matplotlib as matplotlib
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
import allel
from pysam import VariantFile

from bokeh.models import ColumnDataSource, HoverTool
from bokeh.io import output_file, save, export_png, output_notebook, show
from bokeh.plotting import figure, show
from bokeh.layouts import row,  gridplot, column
from bokeh.palettes import Spectral6
output_notebook()

import ipywidgets as widgets
from ipywidgets import interact, interact_manual

from collections import Counter

from sklearn.datasets import make_blobs
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_samples, silhouette_score


import matplotlib.pyplot as plt
import matplotlib.cm as cm
import numpy as np


random.seed(42)
fig = plt.figure() 


Loading BokehJS ...

<Figure size 432x288 with 0 Axes>

In [2]:
coding = {
    'Ethnic background': {
        -1: 'Do not know',
        -3: 'Prefer not to answer',
        1: 'White',
        1001: 'British',
        1002: 'Irish',
        1003: 'Any other white background',
        2: 'Mixed',
        2001: 'White and Black Caribbean',
        2002: 'White and Black African',
        2003: 'White and Asian',
        2004: 'Any other mixed background',
        3: 'Asian or Asian British',
        3001: 'Indian',
        3002: 'Pakistani',
        3003: 'Bangladeshi',
        3004: 'Any other Asian background',
        4: 'Black or Black British',
        4001: 'Caribbean',
        4002: 'African',
        4003: 'Any other Black background',
        5: 'Chinese',
        6: 'Other ethnic group',
    },
    'Gender': {
        0: 'Female',
        1: 'Male',
    }
}
colors ={
    'British': '#CA4399',
    'Irish': '#ff4359',
    'White': '#efa0cf',
    'Pakistani': '#049935',
    'Caribbean': '#364F8B',
    'Chinese': '#906BAF',
    'Indian': '#801A2F',
    'African': '#00bfd9',
    'Patients':'#7DBD91',
    'Controls':'#00bfd9'
}
regions = ['British','Irish','White',
           'Pakistani','Caribbean','Chinese',
           'Indian','African']
subType = ['Patients','Controls' ]

markers ={
    'British': 'circle',
    'Irish': 'circle',
    'White': 'o',
    'Pakistani': 'v',
    'Caribbean': '*',
    'Chinese': '*',
    'Indian': 'v',
    'African': 'v',
    'Patients':'*',
    'Controls':'circle'
}

# NEED TO CHANGE 

In [3]:
# Working directory
path = '/Users/aisha/Desktop/Final/flashPCA/'
path2 = '/Users/aisha/Desktop/Final/'

# Global varialbles
global PCA_data
global combined
global disease_xD, disease_yD
global control_xD, control_yD

In [4]:
# import xml.etree.ElementTree as ETree
  
# # give the path where you saved the xml file
# # inside the quotes
# xmldata = '/Users/aisha/Desktop/flashPCA_dontRun/Chronic/Chronic_snp_result.xml'
# prstree = ETree.parse(xmldata)
# root = prstree.getroot()
  
# # print(root)
# store_items = []
# all_items = []

# # [print(elem.tag) for elem in root.iter()]

# genes= []
# # GENE_Name = root.findall("./DocumentSummary/GENES/GENE_E/NAME")
# # for gene in GENE_Name:
# #     genes.append(gene.text)

# GENE_Name = root.findall("./DocumentSummary")
# for gene in GENE_Name:
#     store_items = [gene.attrib['uid'], gene[7][0][0].text]
#     all_items.append(store_items)


# # for storeno in root: 
# #     store_Nr = storeno.attrib.get('uid')
# #     itemsF = storeno.find('SNP_ID').text 
# #     store_Nr = storeno.attrib.get('uid')
  
# #     store_items = [store_Nr]
# #     all_items.append(store_items)
  
# SNPs = pd.DataFrame(all_items, columns=['uid', 'gene'])
# SNPs['uid'] = 'rs' +SNPs['uid']
# # SNPs.to_csv(r'/Users/aisha/Desktop/snps.txt', header=None, index=None, sep=' ', mode='a')

# print(SNPs)

# Generate the data for specific disease

# list of data

In [5]:
# Load all diseases names from the working directory  
diseaseName = os.listdir(path)
diseaseName.remove('.DS_Store')
diseaseName.remove('codes')
diseaseName

['Chronic',
 'Cerebrovascular',
 'Breast',
 'myocardial',
 'Colon',
 'Inflammatory',
 'CAD',
 'diabetes',
 'GALC',
 'Atrial',
 'pancreas',
 'DSP',
 'MYO15A']

# select data

In [6]:
# Import Ethnic background of all individuals
EthnicBackground = pd.read_csv(path2 + 'flashpca_S/ukb45833_ethnicity_gender.tsv', delimiter='\t').set_index('eid')
EthnicBackground

21000-0.0  22001-0.0
eid                          
1000017     1001.0        1.0
1000025     1001.0        1.0
1000038     1001.0        1.0
1000042     1001.0        1.0
1000056     1001.0        1.0
...            ...        ...
5861036     1001.0        0.0
5861048     1001.0        0.0
5861055     1001.0        1.0
5861060     1001.0        0.0
5861072     1001.0        0.0

[486107 rows x 2 columns]

In [7]:
# Read each disease files line by line
PCA_data = {}
Controls = {}
for i in diseaseName:
    PCA_data[i] = pd.read_csv(path +i+'/pcs.txt', sep=r'\s+').set_index('FID')
    Controls[i] = pd.read_csv(path +i+'/control_ids.txt', sep=r'\s+', header = None)

## PCA file load and plot

In [8]:
# Map each Ethnic background ID with its name
EthnicBackground.columns = ['Ethnic background', 'Gender']
for feature in coding:
    EthnicBackground[feature] = EthnicBackground[feature].map(coding[feature])
EthnicBackground

Ethnic background  Gender
eid                              
1000017           British    Male
1000025           British    Male
1000038           British    Male
1000042           British    Male
1000056           British    Male
...                   ...     ...
5861036           British  Female
5861048           British  Female
5861055           British    Male
5861060           British  Female
5861072           British  Female

[486107 rows x 2 columns]

In [9]:
# Merge the Ethnic background table with the PCs Table
for i in diseaseName:
    PCA_data[i] = PCA_data[i].join(EthnicBackground)
    PCA_data[i] = PCA_data[i].dropna()
    PCA_data[i] = PCA_data[i].rename({'iid': 'fid'}, axis=1)

In [10]:
# for the controls tables, clean the table
for i in diseaseName:
    Controls[i] = Controls[i].dropna()
    Controls[i] = [x[:7] for x in Controls[i][0]]
    Controls[i] = pd.DataFrame(Controls[i])
    Controls[i][0] = Controls[i][0].astype(int)
    Controls[i] = Controls[i].set_index(0)
    Controls[i]['type'] = 'Controls'
# create a new dictionary (combined) to have all entries of patients and controls
combined = {}
for i in diseaseName:
    combined[i] = PCA_data[i].join(Controls[i])
    combined[i]['type'] = combined[i]['type'].fillna('Patients')
    combined[i]

In [11]:
ETH = ['British','Irish', 'White','Pakistani','Caribbean','Chinese','Indian','African']

# Dictionary of patients ONLY, any ethnic group > 300 is downsapled
onlyPatientsETH = {}
for i in combined.keys():
    if len(combined[i].loc[combined[i]['type'] == 'Controls']) == 0:
        continue
    onlyPatientsETH[i] = combined[i].loc[combined[i]['type'] == 'Patients']
    onlyPatientsETH[i] = onlyPatientsETH[i].loc[onlyPatientsETH[i]['Ethnic background'].isin(ETH)]
for i in onlyPatientsETH: #sample everything to 500
    print(i)
    for j in np.unique(onlyPatientsETH[i]['Ethnic background']):
        zq = Counter(onlyPatientsETH[i]['Ethnic background'].loc[onlyPatientsETH[i]['Ethnic background'] == j])
        for t in zq.values():
            if t > 500:
                onlyPatientsETH[i].loc[onlyPatientsETH[i]['Ethnic background'] == j] = onlyPatientsETH[i].loc[onlyPatientsETH[i]['Ethnic background'] == j].sample(n=100)
    onlyPatientsETH[i] = onlyPatientsETH[i].dropna()   

Chronic
Cerebrovascular
Breast
myocardial
Colon
Inflammatory
CAD
diabetes
GALC
Atrial
pancreas
DSP
MYO15A


In [12]:
combined['CAD']['type']

FID
1000056    Controls
1000061    Controls
1000074    Controls
1000093    Patients
1000115    Controls
             ...   
5860931    Controls
5860979    Patients
5860995    Controls
5861009    Controls
5861024    Patients
Name: type, Length: 92179, dtype: object

In [13]:
# Dictionary of patients ONLY, any ethnic group > 300 is downsapled
equalCP = {}
for i in combined.keys():
    equalCP[i] = combined[i].copy(deep=True)
for i in equalCP: #sample everything to 500
    for j in np.unique(equalCP[i]['type']):
        c = len(equalCP[i]['type'].loc[equalCP[i]['type'] == 'Controls'])
        p = len(equalCP[i]['type'].loc[equalCP[i]['type'] == 'Patients'])
        zq = min([c, p])
        equalCP[i].loc[equalCP[i]['type'] == j] = equalCP[i].loc[equalCP[i]['type'] == j].sample(n=zq)
    equalCP[i] = equalCP[i].dropna()  

In [14]:
# Print number of participants in each ethnic group
for i in combined.keys():
    print(i)
    print(Counter(onlyPatientsETH[i]['Ethnic background']))
    print('--------------------------------------------')

Chronic
Counter({'Pakistani': 298, 'African': 260, 'Chinese': 107, 'Caribbean': 100, 'Irish': 100, 'British': 100, 'Indian': 100, 'White': 94})
--------------------------------------------
Cerebrovascular
Counter({'Indian': 211, 'Caribbean': 183, 'African': 117, 'British': 100, 'Irish': 100, 'Pakistani': 69, 'Chinese': 34, 'White': 31})
--------------------------------------------
Breast
Counter({'Irish': 170, 'British': 100, 'Indian': 45, 'Caribbean': 34, 'African': 20, 'Chinese': 16, 'Pakistani': 14, 'White': 6})
--------------------------------------------
myocardial
Counter({'Irish': 377, 'Indian': 262, 'Pakistani': 128, 'British': 100, 'Caribbean': 67, 'African': 36, 'White': 23, 'Chinese': 17})
--------------------------------------------
Colon
Counter({'Irish': 295, 'British': 100, 'Caribbean': 49, 'Indian': 39, 'African': 28, 'Chinese': 16, 'Pakistani': 13, 'White': 12})
--------------------------------------------
Inflammatory
Counter({'British': 100, 'Irish': 76, 'Indian': 42

## Bokeh

In [15]:
# Function to select a diseases along with the PCs I wish to plot by ethnic group
disease_xD = {}
disease_yD ={}
def diseaseSelect(disease = 'liver', PC1='U1',PC2='U2'):
    data2 = onlyPatientsETH[disease].copy(deep=True)
    disease_xD[disease + ' ' + PC1 + ' ' + PC2] = data2[[PC1,PC2]].values
    disease_yD[disease + ' ' + PC1 + ' ' + PC2] = data2['Ethnic background'].values

In [16]:
# Run (diseaseSelect) function for all diseases depending on the number of PCs available for them
for i in diseaseName:
    for j in range(1, len(onlyPatientsETH[i].columns)-4):
        diseaseSelect(disease = i, PC1 = 'PC'+str(j), PC2 ='PC'+str(j+1))

In [17]:
# Plot the diseases of the previously selected PCs
@interact
def showDiffChromosome(disease = disease_xD.keys()):
    x = disease_xD[disease] 
    y = disease_yD[disease]
    p = figure(title="Disease: - %s"%( disease), width=800, height=800)
    
    for region in regions:
        sources = ColumnDataSource(data={'eth': y[y==region]}) 
        alpha = 1
        p.scatter(x[y==region].T[0], x[y==region].T[1],
            color=colors.get(region, 'lightgray'),
            marker=markers.get(region),
#             marker = marker,
            size=7,
            alpha=alpha, muted_alpha = 0, legend_label=region#, tooltips=[('Ethnicity', '@Ethnic background')]
                 )
        
        p.add_tools(HoverTool(tooltips=[ ("(x, y)", "($x, $y)")]))
    p.legend.location = "top_right"
    p.legend.click_policy = 'mute'
    
    name = 'dataPlots/Country/'+disease+'.png'
#     export_png(p, filename=name)
    show(p)

interactive(children=(Dropdown(description='disease', options=('Chronic PC1 PC2', 'Chronic PC2 PC3', 'Chronic …

In [18]:
# Function to select a diseases along with the PCs I wish to plot by case (patient, contol)
control_xD = {}
control_yD ={}
control_yyD ={}
def directPlot(disease = 'liver', PC1='PC1',PC2='PC2'):
    data2 = equalCP[disease].copy(deep=True)
    data2 = data2.dropna()
    control_xD[disease + ' ' + PC1 + ' ' + PC2] = data2[[PC1,PC2]].values
    control_yD[disease + ' ' + PC1 + ' ' + PC2] = data2['type'].values
    control_yyD[disease + ' ' + PC1 + ' ' + PC2] = data2['Ethnic background'].values

In [19]:
for i in diseaseName:
    if i not in equalCP.keys():
        print('cont: ' + i)
        continue
    for j in range(1, len(onlyPatientsETH[i].columns)-4):
        directPlot(disease = i, PC1 = 'PC'+str(j), PC2 ='PC'+str(j+1))

In [20]:
directPlot(disease = 'Chronic', PC1 = 'PC2', PC2 ='PC3')

In [21]:
@interact
def showDiffChromosome(plot = control_xD.keys()):
    p = figure(title="chromosome - %s"%( plot), width=1000, height=800)
    x = control_xD[plot] 
    y = control_yD[plot]
    yy =control_yyD[plot]
    
    ## add randomness
    for region in subType:
        marker = 'circle'
        alpha = 1
        v1 = x[y==region].T[0] #+ np.random.randn(len(x[y==region].T[0]))
        v2 = x[y==region].T[1] #+ np.random.randn(len(x[y==region].T[1]))
        print(len(v1))
        p.scatter(v1, v2,
            color=colors.get(region, 'lightgray'),
            marker=markers.get(region),
#             marker = marker,
            size=7,
            alpha=alpha, muted_alpha = 0, legend_label=region
        )
        #sources = ColumnDataSource(data={'eth': y[y==region]}) 
        #p.add_tools(HoverTool(tooltips=[ ("(x, y)", "($x, $y)"), #("Ethnicity", "@eth"),]))
        p.legend.location = "top_right"
        sources = ColumnDataSource(data={'eth': y[y==region]}) 
        p.add_tools(HoverTool(tooltips=[ ("(x, y)", "($x, $y)"), #("Ethnicity", "@eth"),
                                       ]))
    p.legend.click_policy = 'mute'
    name = 'dataPlots/Controls/'+plot+'_samePC.png'
    show(p)
#     export_png(p, filename=name)
    

interactive(children=(Dropdown(description='plot', options=('Chronic PC1 PC2', 'Chronic PC2 PC3', 'Chronic PC3…

In [22]:
keys_new = ['Chronic PC1 PC2', 'Chronic PC2 PC3', 'Chronic PC3 PC4', 'Chronic PC1 PC3', 'pancreas PC2 PC3', 'pancreas PC3 PC4', 'pancreas PC1 PC3' ]

In [23]:
from bokeh.models import CustomJS, Slider, ColumnDataSource,Range1d, LabelSet, Label
from bokeh.transform import factor_cmap, factor_mark
@interact
def showDiffChromosome(plot = keys_new, n_clusters = [2, 3, 4, 5, 6]):

    MARKERS = ['hex', 'circle_x', 'triangle', 'diamond', 'square', 'star']
    COLORS = ['pink', 'red', 'green', ]
    source = pd.DataFrame(dict(
        names=['Mark', 'Amir', 'Matt', 'Greg', 'Owen', 'Juan']
    ))
    
    p = figure(title="%s - %s"%( plot, n_clusters), width=1000, height=800)
    
    X = disease_xD[plot] 
    y = disease_yD[plot]
    
    
    # Initialize the clusterer with n_clusters value and a random generator
    # seed of 10 for reproducibility.
    clusterer = KMeans(n_clusters=n_clusters, random_state=10)
    cluster_labels = clusterer.fit_predict(X)

    # The silhouette_score gives the average value for all the samples.
    # This gives a perspective into the density and separation of the formed
    # clusters
    silhouette_avg = silhouette_score(X, cluster_labels)
    print("For n_clusters =", n_clusters, "The average silhouette_score is :", silhouette_avg)

    # Compute the silhouette scores for each sample
    sample_silhouette_values = silhouette_samples(X, cluster_labels)


    # 2nd Plot showing the actual clusters formed
    color1 = cm.nipy_spectral(cluster_labels.astype(float) / n_clusters)
    p.scatter(
        X[:, 0], X[:, 1], marker="o", size=20, alpha=0.7,  color=color1, muted_alpha = 0.01 
    )

    # Labeling the clusters
    centers = clusterer.cluster_centers_

    for i, c in enumerate(centers):
        p.scatter(c[0], c[1], marker=MARKERS[i], alpha=1, size=0, muted_alpha = 0.01,color='pink')
    


    show(p)

interactive(children=(Dropdown(description='plot', options=('Chronic PC1 PC2', 'Chronic PC2 PC3', 'Chronic PC3…

In [24]:
from bokeh.models import CustomJS, Slider, ColumnDataSource,Range1d, LabelSet, Label
from bokeh.transform import factor_cmap, factor_mark
@interact
def showDiffChromosome(plot = keys_new, n_clusters = [2, 3, 4, 5, 6]):

    p = figure(title="%s - %s"%( plot, n_clusters), width=1000, height=800)

    X = disease_xD[plot] 
    y = disease_yD[plot]

    fig, ( ax2) = plt.subplots(1, 1)
    fig.set_size_inches(20, 16)
    # Initialize the clusterer with n_clusters value and a random generator
    # seed of 10 for reproducibility.
    clusterer = KMeans(n_clusters=n_clusters, random_state=10)
    cluster_labels = clusterer.fit_predict(X)

    # The silhouette_score gives the average value for all the samples.
    # This gives a perspective into the density and separation of the formed
    # clusters
    silhouette_avg = silhouette_score(X, cluster_labels)
    print("For n_clusters =", n_clusters, "The average silhouette_score is :", silhouette_avg)

    # Compute the silhouette scores for each sample
    sample_silhouette_values = silhouette_samples(X, cluster_labels)


    # 2nd Plot showing the actual clusters formed
    color1 = cm.nipy_spectral(cluster_labels.astype(float) / n_clusters)
    ax2.scatter(
        X[:, 0], X[:, 1], marker=".", s=800, lw=0, alpha=0.7, c=color1, edgecolor="k"
    )

    # Labeling the clusters
    centers = clusterer.cluster_centers_
    # Draw white circles at cluster centers
    ax2.scatter(
        centers[:, 0],
        centers[:, 1],
        marker="o",
        c="white",
        alpha=1,
        s=200,
        edgecolor="k",
    )

    for i, c in enumerate(centers):
        ax2.scatter(c[0], c[1], marker="$%d$" % i, alpha=1, s=50, edgecolor="k")

    ax2.set_title("The visualization of the clustered data.")
    ax2.set_xlabel("Feature space for the 1st feature")
    ax2.set_ylabel("Feature space for the 2nd feature")

    plt.suptitle(
            "Silhouette analysis for KMeans clustering on sample data with n_clusters = %d"
            % n_clusters,
            fontsize=14,
            fontweight="bold",
        )

    plt.show()

interactive(children=(Dropdown(description='plot', options=('Chronic PC1 PC2', 'Chronic PC2 PC3', 'Chronic PC3…